In [1]:
import requests
import geopandas as gpd
from shapely.geometry import Polygon
import pandas as pd
from matplotlib import pyplot as plt
import numpy as np
from requests.exceptions import RequestException, HTTPError
import urllib3
from tqdm import tqdm 

In [2]:
# Cargar cdmx
cdmx= gpd.read_file("https://datos.cdmx.gob.mx/dataset/bae265a8-d1f6-4614-b399-4184bc93e027/resource/deb5c583-84e2-4e07-a706-1b3a0dbc99b0/download/limite-de-las-alcaldas.json")
cdmx=cdmx.dissolve(by='CVE_ENT')

In [3]:
bounds = cdmx.total_bounds
min_lng, min_lat, max_lng, max_lat = bounds

print("Min Latitud:", min_lat)
print("Max Latitud:", max_lat)
print("Min Longitud:", min_lng)
print("Max Longitud:", max_lng)

Min Latitud: 19.04823666014711
Max Latitud: 19.59275727980177
Min Longitud: -99.3649242001858
Max Longitud: -98.94030282041224


In [4]:

urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)


def encuentra_cuadrante(lat, lng):
    url = f"https://cuadrantes.ssc.cdmx.gob.mx/api/v1/getcuadrante?lat={lat}&lng={lng}"
    try:
        response = requests.get(url, verify=False)  
        response.raise_for_status()  
        data = response.json()
        if data and data.get('data'):
            return data
        return None
    except (RequestException, HTTPError) as e:
        return None  

def crear_grid(min_lat, max_lat, min_lng, max_lng, step):
    lat_points = np.arange(min_lat, max_lat, step)
    lng_points = np.arange(min_lng, max_lng, step)
    return [(lat, lng) for lat in lat_points for lng in lng_points]

In [5]:
step = 0.001 

grid_points = crear_grid(min_lat, max_lat, min_lng, max_lng, step)
df_general = pd.DataFrame()

for lat, lng in tqdm(grid_points, desc="Procesando puntos del grid"):
    data = encuentra_cuadrante(lat, lng)
    if data:
        try:
            datos_list = data['data'][0]['datos']
            coordenadas_list = data['data'][0]['coordenadas']
            df_temp = pd.DataFrame([datos_list])
            latitudes = []
            longitudes = []
            for i in range(len(coordenadas_list)):
                latitudes.append(coordenadas_list[i][0])
                longitudes.append(coordenadas_list[i][1])
            poligono = Polygon(zip(latitudes, longitudes))
            df_temp['geometry'] = gpd.GeoSeries([poligono])
            df_temp = gpd.GeoDataFrame(df_temp, geometry='geometry')
            df_temp['centroid'] = df_temp['geometry'].centroid
            df_general = pd.concat([df_general, df_temp], ignore_index=True)
            #print(f"Se encontró cuadrante para ({lat}, {lng})")
        except Exception as e:
            print(f"Fallo al procesar ({lat}, {lng}): {e}")
    else:
       
        pass

Procesando puntos del grid:  22%|██▏       | 50940/231625 [2:32:10<11:10:13,  4.49it/s]C:\Users\administracion.sniiv\AppData\Local\Temp\ipykernel_6788\2785815762.py:22: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_general = pd.concat([df_general, df_temp], ignore_index=True)
Procesando puntos del grid:  22%|██▏       | 51604/231625 [2:34:09<11:36:55,  4.31it/s]C:\Users\administracion.sniiv\AppData\Local\Temp\ipykernel_6788\2785815762.py:22: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_ge

In [6]:
#Eliminar idcd repetidos
df_general = df_general.drop_duplicates(subset=['idcd'])
#Columnas en minúsculas
df_general.columns = df_general.columns.str.lower()
df_general

idcd             deleg     zona cvezona  noregion      sector  \
0      1412           TLALPAN      SUR       S         4    TOPILEJO   
241     647        MILPA ALTA  ORIENTE       O         2    TECOMITL   
272     727        MILPA ALTA  ORIENTE       O         2  MILPA ALTA   
277     489        MILPA ALTA  ORIENTE       O         2  MILPA ALTA   
428    1385           TLALPAN      SUR       S         4    TOPILEJO   
...     ...               ...      ...     ...       ...         ...   
19342   160  GUSTAVO A MADERO    NORTE       N         1   CUAUTEPEC   
19369   161  GUSTAVO A MADERO    NORTE       N         1   CUAUTEPEC   
19376   157  GUSTAVO A MADERO    NORTE       N         1   CUAUTEPEC   
19381   152  GUSTAVO A MADERO    NORTE       N         1   CUAUTEPEC   
19409   754  GUSTAVO A MADERO    NORTE       N         1   CUAUTEPEC   

       cvesector  nocuadrante nomenclatura  areakm2  ...  modulos  microzonas  \
0              5            8      S-4.5.8      NaN  ...     None        None   
241            2            4      O-2.2.4    1.191  ...     None        None   
272            1            3      O-2.1.3    0.165  ...     None        None   
277            1            1      O-2.1.1    0.223  ...     None        None   
428            5            7      S-4.5.7      NaN  ...     None        None   
...          ...          ...          ...      ...  ...      ...         ...   
19342          2           10     N-1.2.10    0.674  ...     None        None   
19369          2            2      N-1.2.2    0.443  ...     None        None   
19376          2            8      N-1.2.8    0.895  ...     None        None   
19381          2           14     N-1.2.14    0.375  ...     None        None   
19409          2            1      N-1.2.1    2.590  ...     None        None   

      idsector                                             coords  meta  \
0          261  19.182929,-99.169328|19.182652,-99.171013|19.1...  None   
241         59  19.168546,-98.988436|19.169197,-98.988488|19.1...  None   
272         57  19.197093,-99.063378|19.201865,-99.080213|19.1...  None   
277         57  19.205193,-99.003068|19.205886,-99.003461|19.2...  None   
428        261  19.199536,-99.164823|19.198594,-99.165622|19.1...  None   
...        ...                                                ...   ...   
19342       27  19.556014,-99.146342|19.555882,-99.146283|19.5...  None   
19369       27  19.570664,-99.131129|19.571567,-99.130924|19.5...  None   
19376       27  19.559185,-99.131218|19.559881,-99.13054|19.56...  None   
19381       27  19.559846,-99.130474|19.559785,-99.13045|19.55...  None   
19409       27  19.572508,-99.135555|19.571788,-99.132683|19.5...  None   

                                            bbox  idestatusc  \
0      -99.201085,19.122595,-99.157703,19.186599           1   
241    -99.010471,19.163667,-98.988264,19.191691           1   
272    -99.084505,19.170154,-99.054447,19.201865           1   
277    -99.040046,19.169034,-99.002114,19.207594           1   
428    -99.177217,19.182008,-99.129070,19.228931           1   
...                                          ...         ...   
19342  -99.146641,19.552228,-99.136125,19.560472           1   
19369  -99.144563,19.560375,-99.130924,19.572847           1   
19376  -99.133611,19.559185,-99.124021,19.570664           1   
19381  -99.130540,19.558267,-99.119554,19.568735           1   
19409  -99.136597,19.570236,-99.124199,19.581079           1   

                                                  nextel  \
0      {'idnextel': '62*800*13338', 'telefono': '5546...   
241    {'idnextel': '62*800*12408', 'telefono': '5546...   
272    {'idnextel': '62*800*13796', 'telefono': '5545...   
277    {'idnextel': '62*800*13248', 'telefono': '5546...   
428    {'idnextel': '62*800*13321', 'telefono': '5546...   
...                                                  ...   
19342  {'idnextel': '62*800*11766', 'telefono': '5546...   
19369  {'idnextel':

In [9]:
#Eliminar centroide
df_general=df_general.drop(columns=['centroid'])


In [10]:
#Voltear coordenadas
def swap_coords(coords):
    return [(y, x) for x, y in coords]


df_general['geometry'] = df_general['geometry'].apply(lambda poly: Polygon(swap_coords(list(poly.exterior.coords))))
df_general.head()

idcd       deleg     zona cvezona  noregion      sector  cvesector  \
0    1412     TLALPAN      SUR       S         4    TOPILEJO          5   
241   647  MILPA ALTA  ORIENTE       O         2    TECOMITL          2   
272   727  MILPA ALTA  ORIENTE       O         2  MILPA ALTA          1   
277   489  MILPA ALTA  ORIENTE       O         2  MILPA ALTA          1   
428  1385     TLALPAN      SUR       S         4    TOPILEJO          5   

     nocuadrante nomenclatura  areakm2  ...  camaras  modulos microzonas  \
0              8      S-4.5.8      NaN  ...     None     None       None   
241            4      O-2.2.4    1.191  ...     None     None       None   
272            3      O-2.1.3    0.165  ...     None     None       None   
277            1      O-2.1.1    0.223  ...     None     None       None   
428            7      S-4.5.7      NaN  ...     None     None       None   

    idsector                                             coords  meta  \
0        261  19.182929,-99.169328|19.182652,-99.171013|19.1...  None   
241       59  19.168546,-98.988436|19.169197,-98.988488|19.1...  None   
272       57  19.197093,-99.063378|19.201865,-99.080213|19.1...  None   
277       57  19.205193,-99.003068|19.205886,-99.003461|19.2...  None   
428      261  19.199536,-99.164823|19.198594,-99.165622|19.1...  None   

                                          bbox idestatusc  \
0    -99.201085,19.122595,-99.157703,19.186599          1   
241  -99.010471,19.163667,-98.988264,19.191691          1   
272  -99.084505,19.170154,-99.054447,19.201865          1   
277  -99.040046,19.169034,-99.002114,19.207594          1   
428  -99.177217,19.182008,-99.129070,19.228931          1   

                                                nextel  \
0    {'idnextel': '62*800*13338', 'telefono': '5546...   
241  {'idnextel': '62*800*12408', 'telefono': '5546...   
272  {'idnextel': '62*800*13796', 'telefono': '5545...   
277  {'idnextel': '62*800*13248', 'telefono': '5546...   
428  {'idnextel': '62*800*13321', 'telefono': '5546...   

                                              geometry  
0    POLYGON ((-99.16933 19.18293, -99.17101 19.182...  
241  POLYGON ((-98.98844 19.16855, -98.98849 19.169...  
272  POLYGON ((-99.06338 19.19709, -99.08021 19.201...  
277  POLYGON ((-99.00307 19.20519, -99.00346 19.205...  
428  POLYGON ((-99.16482 19.19954, -99.16562 19.198...  

[5 rows x 23 columns]

In [11]:
df_general.to_file("cuadrantes_final.geojson", driver='GeoJSON')